# <center> Sentinel-1 and Sentinel-2 Preprocessing in `Python` and `SNAP`</center> 
<center>
    Contact: Ewelina Dobrowolska - <a href="mailto:Ewelina.Dobrowolska@serco.com"> Ewelina.Dobrowolska@serco.com</a> 
    <br> 
    The following training material has been prepared by Serco Italia S.p.A.</a>
    <br> This work is licensed under a <a href="https://creativecommons.org/licenses/by-nc-sa/4.0/"> Creative Commons Attribution-NonCommercial-ShareAlike 4.0 International License
</center>
<br>

<div class="alert alert-block alert-info">
<b>Tip:</b> More information on the characteristics of Sentinel-1 and Sentinel-2 can be found <a href="https://sentinel.esa.int/web/sentinel/missions"> here </a>
</div>

<p style='text-align: justify;'>The pre-processing will be implemented using Python code that can be found in this Jupyter Notebook. Although highly recommended, the exercise <strong>DOES NOT</strong> require any Python programming skills and can be followed by any participant. You will not be asked to write any code but to follow the methodology and understand the processing steps. If you are new to Python or Jupyter Notebooks, here are some references that may help you:
    
- [Python Tutorial](https://www.python.org/about/gettingstarted/)
- [Jupyter Notebook documentation](https://jupyter.readthedocs.io/en/latest/index.html)
- [Jupyter Notebook tutorial](https://jupyter-notebook.readthedocs.io/en/stable/notebook.html)
    
The exercise is divided in the following sections:
1. Load Python modules
2. Sentinel-1 Pre-processing with GPT
 * 2.1 User input data and parameters
 * 2.2 Load input data
 * 2.2 Pre-process new data
 * 2.3 Visualize a single pre-processed product subset
3. Sentinel-2 preprocessing using `snappy`<i>
 * 3.1 User input data and parameters
 * 3.2 Load input data
 * 3.3 Pre-process new data
 * 3.4 Visualize a single pre-processed product subset RGB composite 
    
Let's now start the exercise by loading all the modules. </p>

<font size="5" color="#8b1900"  face="verdana"> <B>1. Load Python modules</B></font>

<div class="alert alert-block alert-info">
<b>Tip:</b> To run the code, click in the code cell you want to run and press <span style="background-color: #D3D3D3">CTRL</span> + <span style="background-color: #D3D3D3">ENTER</span>. Alternatively, you can also go to `Run -> Run Selected Cells`
</div>

In [ ]:
# MODULE                                               # DESCRIPTION     
import matplotlib.image as mpimg                       # create visualizations
import matplotlib.pyplot as plt                        # create visualizations
from zipfile import ZipFile                            # zip file manipulation
import os                                              # data access in file manager  
from glob import iglob                                 # data access in file manager
from osgeo import gdal                                 # library for raster and vector geospatial data format
import pandas as pd                                    # data analysis and manipulation
import numpy as np                                     # scientific computing 
import snappy_esa                                          # SNAP python interface
import math                                            # core module for mathematical functions
import re                                              # this module provides regular expression matching operations
import io                                              # the io module provides Python’s main facilities for dealing with various types of I/O
import shlex                                           # implements a class for parsing simple shell-like syntaxes
from termcolor import colored                          # prints colored text
import subprocess 
from subprocess import Popen, PIPE                     # allows you to spawn new processes
from datetime import datetime                          # supplies classes for manipulating dates and times
from skimage import exposure                           # Skimage module for histogram manipulation
import cv2
snappy_esa.config.set("DEFAULT", "java_max_mem", "20G")
pd.options.display.max_colwidth = 80                   # Longer text in pd.df
# turns on 'nline plotting', where plot graphics will appear in the notebook below the cell that produced them
%matplotlib inline      
#snappy_esa.config.set("DEFAULT", "java_max_mem", "25G")
print('All modules loaded')                            # inform user once packages are loaded

<font size="5" color="#8b1900"  face="verdana"> <B>2. Sentinel-1 Pre-processing: `GPT`

In this step we will pre-process the data using `Sentinel1Denoised` software and the `Science Toolbox Exploitation Platform (SNAP)` in the form of a SNAP GPT graph file and the snappy python package (SNAP-Python interface)

<div class="alert alert-block alert-info">
<b>Tip:</b> More information on the GPT processing tool can be found: <a href="https://senbox.atlassian.net/wiki/spaces/SNAP/pages/70503475/Bulk+Processing+with+GPT"> here </a>
</div>

<font size="4" color="#8b1900"  face="verdana">2.1 User input data and parameters</font>

The paths to the required input and output folders, as well as input parameters for data pre-processing are provided in this section.

In [ ]:
# Direcory containing downloaded zipped Sentinel-1 IW GRD products
input_directory_S1 = '/home/eoafrica/resources/AEO0222_TimeSeries_S1_S2/Data/S1/'
# Directory where preprocessed products will be saved
prep_directory_S1 = './Processing/S1/'
# SNAP graph file adapted for use with python
graph_file_path ='./Processing/Graph_S1_prep_db.xml'

#Parameters
specle_filer = 'Lee' # Valid values are ('Boxcar', 'Median', 'Frost', 'Gamma Map', 'Lee')
speckle_windowsize = '3' # Parameter used in the Gray Speckle filter operator 
proj = 'EPSG:32630'  # Final product projection (used in Terrain Correction op.)
dem = 'SRTM 1Sec HGT' # Digital Elevation Model (used in Terrain Correction op.)
subset_polygon = 'POLYGON ((-6.150094509124756 37.04116439819336, -6.027195930480957 37.04116439819336, -6.027195930480957 36.98495864868164, -6.150094509124756 36.98495864868164, -6.150094509124756 37.04116439819336, -6.150094509124756 37.04116439819336))'
out_format = 'GeoTIFF' # Available formats - 'GeoTIFF', 'BEAM-DIMAP'

Below we specify some usefull functions used in further processing.

In [ ]:
# Get format suffix
if out_format == 'GeoTIFF': suffix = '.tif'
elif out_format == 'BEAM-DIMAP': suffix = '.dim'
else: print('Please sellect one of the available formats - GeoTIFF, BEAM-DIMAP')

In [ ]:
# Adds a quotation mark to string (for use in command line (cmd)) - needed to run the SNAP graph
def dq(s):
    return '"' + s + '"'

# Call a terminal and execute a command and print the terminal output in the output cell.
def execute(command):
    with Popen(shlex.split(command), stdout=PIPE, bufsize=1, universal_newlines=True) as p:
        while True:
            line = p.stdout.readline()
            if not line:
                break
            print(line)    
        exit_code = p.poll()
    return exit_code

<font size="4" color="#8b1900"  face="verdana"> 2.2 Load input data</font>

In this step, a database of all input products will be created including the product name, date of acquisition, product type, the preprocessing status and other parameters. 

In [ ]:
# Create a list of downloaded Sentinel-1 products available in the input directory in .SAFE format (unzipped)
input_S1_files = list(iglob(os.path.join(input_directory_S1, '*S1*.SAFE'), recursive=True))
input_S1_files.sort(key = lambda x: x.split('_')[-4]) # Sort the product list by date of acquisition
name, date, mode, product_type, polarization, band_names, preprocessed = ([] for i in range(7))
f = 0
for i in input_S1_files: # Loop over downloaded Sentinel-1 products available in the input directory
    f+=1
    # Read products with snappy module
    s1_read = snappy_esa.ProductIO.readProduct(i.replace(".SAFE", ".SAFE/manifest.safe"))
    s1_name = s1_read.getName() # Get product name
    ac_date = re.split('_|T',s1_name)[4] # Get product acquisition date
    date.append(datetime.strftime(datetime.strptime(ac_date, '%Y%m%d'),'%d %b. %Y'))
    name.append(s1_name)
    mode.append(s1_name.split("_")[1])
    product_type.append(s1_name.split("_")[2])
    polarization.append(s1_name.split("_")[3])
    # Get raster dimensions and band names
    band_names.append(s1_read.getBandNames())
    s1_read.dispose()
    # Check if preprocessed products are available in the Output directory
    proc = os.path.join(prep_directory_S1, os.path.basename(i).split('T')[0] + '_prep' + suffix)
    if os.path.isfile(proc):
        preprocessed.append(True)
    else:
        preprocessed.append(False)
             
# Create the input data dataframe
df_s1_data = pd.DataFrame({'Name': name, 'Date': date, 'Sensing Mode': mode,'Product Type': product_type, 'Polarization': polarization, 'Available Bands': band_names, 'Preprocessed': preprocessed})
display(df_s1_data)

<font size="4" color="#8b1900"  face="verdana"> 2.3 Preprocess new data </font>

In this step we use the dataframe created in previous step, to process products for which no pre-procesessed product exists. 

<div class="alert alert-block alert-info">
<b>Tip:</b> SNAP EO Data Processors are implemented as GPF operators and can be invoked via the Windows or UNIX command-line using the GPF Graph Processing Tool - GPT - which can be found in the bin directory of your SNAP installation.
</div>

For each product together with other pre-defined parameters will be use as an input for the following SNAP GPT graph: 
<br><br>
<center><img src=Images/Processing_S_1_graph.png width="1400"/></center>
<br>

*Depending on your machine computation capacity this step (preprocessing) can take several minutes.*

In [ ]:
prep_data_S1 = [] # Create a list of preprocessed image paths for further use
for index, row in df_s1_data.iterrows():  # Iterate over the rows of the data frame
    s1 = os.path.join(input_directory_S1, row['Name'] + '.SAFE') # Re-create path to the original zipped product
    if row['Preprocessed']:  # Check if pre-processed product exists, if YES then append it's path to the list
        print(colored('Product ' + row['Name'] + ' is already pre-processed!', 'green'))
        prep_data_S1.append(os.path.join(prep_directory_S1, row['Name'].split('T')[0] + '_prep' + suffix))
    else: # If pre-processed product does not exist 
        print(colored('Pre-processing product ' + row['Name'] + '!', 'red'))   
        start = datetime.now()
        ### Process graph
        # Define output product name and path
        out_path_S1 = os.path.join(prep_directory_S1, os.path.basename(s1).split('T')[0] + '_prep' + suffix)
        # Create the command to be passed to the terminal 
        cmd_parts = ['gpt', dq(graph_file_path), "-PInput=" + dq(s1),
                     "-PSpeckle_Filter=" + dq(specle_filer),"-PWindow_size=" + dq(speckle_windowsize),
                     "-PDEM=" + dq(dem), "-PCSR=" + dq(proj), 
                     "-PPolygon=" + dq(subset_polygon),
                     "-POutput=" + dq(out_path_S1), "-PFormat=" + dq(out_format)]
        code = execute(' '.join(cmd_parts)) # Execute the command in the terminal
        df_s1_data.at[index,'Preprocessed'] = True  # When preprocessing is finished update the data frame
        prep_data_S1.append(out_path_S1) # Append the path to the list of preprocessed images
        end = datetime.now()
        print(colored('Product ' + row['Name'] + ' sucessfuly pre-processed in '+ str(end - start) + '!', 'green'))

<font size="4" color="#8b1900"  face="verdana"> 2.4 Visualize a single pre-processed product subset </font>

In [ ]:
# Get list of band names
prep_vis = snappy_esa.ProductIO.readProduct(prep_data_S1[-1])
bands = list(prep_vis.getBandNames())

# Create a figure to visualize the input data
fig = plt.figure(figsize = (17,20))
fig.tight_layout(w_pad=1, h_pad=1)
d = math.ceil(math.sqrt(len(bands))) 

# Visualize each band
for band in range(1, len(bands)+1): 
    # lets only visualise a subset of the data
    vis = prep_vis.getBand(bands[band-1])
    # get the widtth and height of the images
    width = vis.getRasterWidth()  
    height = vis.getRasterHeight()
    # Read the pixel values into numpy array 
    vis = vis.readPixels(0,0,width,height,np.zeros(width*height, dtype = np.float32))
    vis.shape = height, width   # reshape the numpy array 
    # Create add a subplot and visualize the band
    ax = fig.add_subplot(d,d,band)
    ax.title.set_text(bands[band-1])
    vis[vis == 0.0] = np.nan
    ax.imshow(vis, cmap= 'gray', vmin =np.nanpercentile(vis, 5), vmax = np.nanpercentile(vis, 95)) 

<font size="5" color="#8b1900"  face="verdana"> <B>3. Sentinel-2 Pre-processing: `snappy`

The easiest way to know which operators are available in `snappy` is to call `gpt -h` from command line, which will output the list. If you want to access the documentation of a specific operator, use `gpt -h *Operator*.

<font size="4" color="#8b1900"  face="verdana">3.1 User input data and parameters</font>

The paths to the required input and output folders, as well as input parameters for data pre-processing are provided in this section.

In [ ]:
# Direcory containing downloaded zipped Sentinel-2 Level-2A products
input_directory_S2 = '/home/eoafrica/resources/AEO0222_TimeSeries_S1_S2/Data/S2/'
# Directory where preprocessed products will be saved
prep_directory_S2 = './Processing/S2/'

#Parameters
target_res = 10
band_subset = 'B2,B3,B4,B8,B11,B12'  # Enter bands without spaces, if you want to use all bands, set to 'All' 
polygon_wkt = 'POLYGON ((-6.150094509124756 37.04116439819336, -6.027195930480957 37.04116439819336, -6.027195930480957 36.98495864868164, -6.150094509124756 36.98495864868164, -6.150094509124756 37.04116439819336, -6.150094509124756 37.04116439819336))'
out_format = 'GeoTIFF' # Available formats - 'GeoTIFF', 'BEAM-DIMAP'

In [ ]:
# Get format suffix
if out_format == 'GeoTIFF': suffix = '.tif'
elif out_format == 'BEAM-DIMAP': suffix = '.dim'
else: print('Please sellect one of the available formats - GeoTIFF, BEAM-DIMAP')

<font size="4" color="#8b1900"  face="verdana"> 3.2 Load input data</font>

In this step, a database of all input products will be created including the product name, date of acquisition, product type, the preprocessing status and other parameters. 

In [ ]:
# Create a list of downloaded zipped Sentinel-2 products available in the input directory
input_S2_files = list(iglob(os.path.join(input_directory_S2, '*S2*.SAFE'), recursive=True))
input_S2_files.sort(key = lambda x: x.split('_')[-4]) # Sort the product list by date of acquisition
name, date, product_type, preprocessed = ([] for i in range(4))
f = 0
for i in input_S2_files: # Loop over downloaded Sentinel-2 products available in the input directory
    f+=1
    # Read zipped product with snappy
    s2_read = snappy_esa.ProductIO.readProduct(i.replace(".SAFE", ".SAFE/MTD_MSIL2A.xml"))
    s2_name = s2_read.getName() # Get product name
    ac_date = re.split('_|T',s2_name)[2] # Get product acquisition date
    date.append(datetime.strftime(datetime.strptime(ac_date, '%Y%m%d'),'%d %b. %Y'))
    name.append(s2_name)
    product_type.append(s2_name.split("_")[1])
    s2_read.dispose()
    # Check if preprocessed products are available in the Output directory
    proc = os.path.join(prep_directory_S2, os.path.basename(i).split('T')[0] + '_prep' + suffix)
    if os.path.isfile(proc):
        preprocessed.append(True)
    else:
        preprocessed.append(False)
        
# Create the input data dataframe
df_s2_data = pd.DataFrame({'Name': name, 'Date': date,'Product Type': product_type, 'Preprocessed': preprocessed})
display(df_s2_data)

<font size="4" color="#8b1900"  face="verdana"> 3.3 Preprocess new data </font>

Here our original products will be resampled and subset of the whole scene to study area will be created and stored for later analyses.  Following processing steps will be performed: 
* Resampling 
* Subset<br>

Reasampling and subset of Sentinel-2 image will be performed using *snappy* module in Python. Resampling process is needed to make computations across different bands of the image as well as to create raster stack later. Image subset will allow to not only cut the whole image to just study area but also will make possible to store only bands needed for later analyses in order to reduce the memory requirements and limit the computation time. Only subset product will be stored physically in the Virtual Machine. <br>


*Depending on your machine computation capacity this step (resampling and subset) can take several minutes.*

In [ ]:
prep_data_S2 = [] # Create a list of preprocessed image paths for further use
for index, row in df_s2_data.iterrows():  # Iterate over the rows of the data frame created in step 4.
    s2 = os.path.join(input_directory_S2, row['Name'] + '.SAFE') # Re-create path to the original zipped product
    if row['Preprocessed']:  # Check if pre-processed product exists, if YES then append it's path to the list
        print(colored('Product ' + row['Name'] + ' is already pre-processed!', 'green'))
        prep_data_S2.append(os.path.join(prep_directory_S2, row['Name'].split('T')[0] + '_prep' + suffix))
    else: # If pre-processed product does not exist 
        print(colored('Pre-processing product ' + row['Name'] + '!', 'red'))   
        start = datetime.now()  
        out_path_S2 = os.path.join(prep_directory_S2, os.path.basename(s2).split('T')[0] + '_prep' + suffix)
        s2_read = snappy_esa.ProductIO.readProduct(s2)
        s2_name = s2_read.getName()
        #Resample product
        parameters = snappy_esa.HashMap()
        parameters.put('targetResolution', target_res)
        resample = snappy_esa.GPF.createProduct('Resample', parameters, s2_read)
        #Create subset from resampled product and store it 
        parameters = snappy_esa.HashMap()
        parameters.put('copyMetadata', True)
        if band_subset != 'All':
            parameters.put('sourceBands', band_subset)
        parameters.put('geoRegion', polygon_wkt) #set height and weight of the raster band for all the bands 
        subset = snappy_esa.GPF.createProduct('Subset', parameters, resample) #perform subset using as input file resampled product
        # Write the product
        snappy_esa.ProductIO.writeProduct(subset, out_path_S2, out_format) #saving subset asformat
        
        df_s2_data.at[index,'Preprocessed'] = True  # When preprocessing is finished update the data frame
        prep_data_S2.append(out_path_S2) # Append the path to the list of preprocessed images
        end = datetime.now()
        print(colored('Product ' + row['Name'] + ' sucessfuly pre-processed in '+ str(end - start) + '!', 'green'))

<font size="4" color="#8b1900"  face="verdana"> 3.4 Visualize a single pre-processed product subset RGB composite </font>

In [ ]:
# Get list of band names
prep_vis = snappy_esa.ProductIO.readProduct(prep_data_S2[5]) # For example we wisualize the fifth preprocessed product
bands = list(prep_vis.getBandNames())

# Load 3 bands you wish to use for the RGB composite - Here we create the natural color composite using bands B2, B3 and B4
red = prep_vis.getBand('B4')
green  = prep_vis.getBand('B3')
blue = prep_vis.getBand('B2')

# get the widtth and height of the images
width = red.getRasterWidth()  
height = red.getRasterHeight()

# Read the pixel values into numpy array 
red = red.readPixels(0,0,width,height,np.zeros(width*height, dtype = np.float32))
green = green.readPixels(0,0,width,height,np.zeros(width*height, dtype = np.float32))
blue = blue.readPixels(0,0,width,height,np.zeros(width*height, dtype = np.float32))

# reshape the numpy array 
red.shape = height, width
blue.shape = height, width
green.shape = height, width

# create a stack
rgbArray = np.stack((red,green,blue),axis=2) 
 
# Histogram equalization is a method in image processing of contrast adjustment using the image's histogram. 
# Stretching the histogram can improve the contrast of a displayed image by eliminating very high or low reflectance 
# values that skew the display of the image.
pLow, pHigh = np.percentile(rgbArray[~np.isnan(rgbArray)], (2.5,100-2.5))
img_rescale = exposure.rescale_intensity(rgbArray, in_range=(pLow,pHigh))

# Create a figure and visualize our data
fig = plt.figure(figsize = (17,17))
plt.imshow(img_rescale)